# Python with PostgreSQL & PostGIS

<span style="color: blue;">Note: Please always run the complete Jupyter Notebook from the beginning, as object names such as 'sql' and 'gdf' are reused in the code cells.</span>

## Libraries and Settings

In [148]:
# Libraries
import os
import folium
import pandas as pd
import geopandas as gpd
from sqlalchemy import create_engine, text

# Ignore warnings
import warnings
warnings.filterwarnings("ignore")

print(os.getcwd())

/workspaces/python_postgresql_postgis


## Create database connection

In [149]:
# Set up database connection
user = "pgadmin"
password = "geheim"
host = "localhost"
port = "5432"
database = "osm_switzerland"

# Create Connection URL
db_connection_url = "postgresql://" + user + ":" + password +\
                    "@" + host + ":" + port + "/" + database

# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)

# Test database connection
with engine.connect() as connection:
    result = connection.execute(text('SELECT current_database()'))
    print(result.fetchone())

# Dispose the engine
engine.dispose()

('osm_switzerland',)


## List tables in database

In [150]:
# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)

# Open a connection
with engine.connect() as connection:

    # Execute the query
    result = connection.execute(text("""SELECT table_name
                                        FROM information_schema.tables
                                        WHERE table_schema = 'public';"""))
    
    # Fetch and print the results
    for row in result:
        print(row[0])

# Dispose the engine
engine.dispose()

geography_columns
geometry_columns
spatial_ref_sys
planet_osm_line
planet_osm_point
planet_osm_roads
planet_osm_polygon


## Show columns and data types of selected table

In [151]:
# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)

# Specify your table name
table_name = 'planet_osm_polygon'

# Query to get column information
query = f"""SELECT column_name, data_type 
        FROM information_schema.columns 
        WHERE table_name = '{table_name}'"""

# Execute the query and read the result into a DataFrame
df = pd.read_sql(query, engine)

# Dispose the engine
engine.dispose()

# Print the DataFrame
df

column_name     data_type
0             osm_id        bigint
1            z_order       integer
2           way_area          real
3                way  USER-DEFINED
4   addr:housenumber          text
..               ...           ...
68              wood          text
69         tracktype          text
70            access          text
71    addr:housename          text
72       addr:street          text

[73 rows x 2 columns]

## Query: Select buildings for which full address is available in defined zip code areas

In [152]:
# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)

# Define SQL query 
sql = """SELECT
                p.osm_id,
                p."addr:street",
                p."addr:housenumber",
                p."addr:city",
                p."addr:postcode",
                p.building,
                st_transform(p.way, 4326) AS geom
        FROM
                public.planet_osm_polygon AS p
        WHERE
                p."addr:street" IS NOT NULL
                AND p."addr:housenumber" IS NOT NULL
                AND p."addr:city" IS NOT NULL
                AND p."addr:postcode" IN ('8001', '8002')"""

# Query the database and store the result in a GeoDataFrame
gdf = gpd.GeoDataFrame.from_postgis(sql, engine)

# Dispose the engine
engine.dispose()

# Print the GeoDataFrame
gdf


osm_id          addr:street addr:housenumber addr:city addr:postcode  \
0     501215139      Weinbergstrasse              42c    Zürich          8001   
1     501215142      Weinbergstrasse              41c    Zürich          8001   
2     157954139         Löwenstrasse               67    Zürich          8001   
3     157954140         Löwenstrasse               69    Zürich          8001   
4     316823317         Bahnhofplatz               12    Zürich          8001   
...         ...                  ...              ...       ...           ...   
2350  108633058  Brandschenkestrasse              152    Zürich          8002   
2351  108633096  Brandschenkestrasse             152c    Zürich          8002   
2352  108633055  Brandschenkestrasse             152b    Zürich          8002   
2353  108626600  Brandschenkestrasse             110a    Zürich          8002   
2354   34572240  Brandschenkestrasse              110    Zürich          8002   

        building                                               geom  
0           None  POLYGON ((8.54415 47.38017, 8.54417 47.3801, 8...  
1           None  POLYGON ((8.54403 47.38013, 8.54405 47.38006, ...  
2     commercial  POLYGON ((8.53805 47.37717, 8.53808 47.37716, ...  
3     commercial  POLYGON ((8.53813 47.37725, 8.5383 47.37718, 8...  
4     commercial  POLYGON ((8.53819 47.37733, 8.5382 47.37732, 8...  
...          ...                                                ...  
2350  industrial  POLYGON ((8.52413 47.36489, 8.52415 47.36477, ...  
2351      office  POLYGON ((8.52388 47.36409, 8.52391 47.3639, 8...  
2352  industrial  POLYGON ((8.5239 47.36435, 8.5239 47.36431, 8....  
2353      office  POLYGON ((8.52458 47.3655, 8.52462 47.36534, 8...  
2354  commercial  POLYGON ((8.52469 47.36579, 8.52476 47.36552, ...  

[2355 rows x 7 columns]

## Show selected features on map

<span style="color: blue;">Note the popup field in the map, which has been added to provide additional information about buildings.</span>

<span style="color: blue;">Example of alternative background maps (maptiles) are:</span>
- <span style="color: blue;">EsriWorldImagery</span>
- <span style="color: blue;">EsriWorldTopoMap</span>
- <span style="color: blue;">EsriWorldGrayCanvas</span>
- <span style="color: blue;">CartoDBDarkMatter</span>
- <span style="color: blue;">CartoDBPositron</span>


In [153]:
# Ensure the GeoDataFrame has the correct projection (EPSG:4326)
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)
else:
    pass

# Calculate the mean longitude and latitude for the map center
centroids = gdf.geometry.centroid
lon = centroids.x.mean()
lat = centroids.y.mean()

# Initialize the map
m = folium.Map(location=[lat, lon], 
               zoom_start=15,
               tiles='EsriWorldImagery')

# Map settings
folium.GeoJson(
    gdf,
    name='geojson',
    weight=0.5,
    fill_color='greenyellow',
    fillOpacity=0.8,
    popup=folium.GeoJsonPopup(fields=['addr:street',
                                      'addr:housenumber',
                                      'addr:city',
                                      'addr:postcode',
                                      'building'])
).add_to(m)

folium.LayerControl().add_to(m)

# Plot map
m

## Query: Select coffee stores in Switzerland

In [154]:
# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)  

# Define SQL query
sql = """SELECT
            h.osm_id,
            h.shop,
            h.name,
            ST_Transform(h.way, 4326) AS geom
        FROM planet_osm_point h
        WHERE h.shop = 'coffee';""" # key = value

# Query the database and store the result in a GeoDataFrame
gdf = gpd.GeoDataFrame.from_postgis(sql, engine)

# Dispose the engine
engine.dispose()

# Print the GeoDataFrame
gdf


osm_id    shop                               name  \
0     4929337494  coffee                          Badilatti   
1     4929338163  coffee  Rocca & Zgraggen Gastro-Maschinen   
2     9999220377  coffee                        Presto Café   
3     2473998249  coffee                   Pappy John & Cie   
4     9935502918  coffee                  The Greek Project   
..           ...     ...                                ...   
113   8463666946  coffee                             Tchibo   
114   5019777080  coffee                              KAFOJ   
115   7562485062  coffee                          Nespresso   
116  10606177703  coffee                Kaffee Macher:innen   
117   8909393062  coffee                          Moccaraba   

                         geom  
0     POINT (9.9654 46.59732)  
1    POINT (9.96413 46.59663)  
2    POINT (6.67867 46.52378)  
3    POINT (6.65236 46.52688)  
4    POINT (6.63765 46.51983)  
..                        ...  
113  POINT (7.61409 46.74435)  
114   POINT (7.2462 47.14107)  
115  POINT (7.59167 47.55363)  
116   POINT (7.5891 47.54444)  
117  POINT (7.59199 47.56274)  

[118 rows x 4 columns]

## Show selected features on map

In [155]:
# Ensure the GeoDataFrame has the correct projection (EPSG:4326)
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)
else:
    pass

# Calculate the mean longitude and latitude for the map center
centroids = gdf.geometry.centroid
lon = centroids.x.mean()
lat = centroids.y.mean()

# Initialize the map
m = folium.Map(location=[lat, lon], 
               zoom_start=9, 
               tiles='EsriWorldTopoMap')

# Map settings
folium.GeoJson(
    gdf,
    name='map',
    popup=folium.GeoJsonPopup(fields=['name', 'shop'])
).add_to(m)

folium.LayerControl().add_to(m)

# Plot map
m

## Query: Select all supermarkets in a distance of 1000m around the central station in the city of Winterthur.

<span style="color: blue;">Note:</span>

<span style="color: blue;">For each supermarket, the distance to the central station in meters is calculated and stored as new column 'distance_meters'.</span>

<span style="color: blue;">In addition, a popup field was added to the map, allowing users to view detailed information about each selected feature when they click on it.</span>

<span style="color: blue;">The WGS84 (World Geodetic System 1984) coordinates in ST_MakePoint(LON, LAT) were derived from: https://tools.retorte.ch/map.</span>


In [156]:
# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)  

# Define SQL query
sql = """SELECT
            p.osm_id,
            p.shop,
            p.name,
            ST_Distance(
                ST_Transform(p.way, 4326)::geography,
                -- Central station coordinates
                ST_SetSRID(ST_MakePoint(8.58309, 47.31763), 4326)::geography 
            ) AS distance_meters,
            ST_TRANSFORM(p.way, 4326) AS geom
        FROM
            planet_osm_point AS p
        WHERE
            p.shop = 'supermarket'
            AND ST_DWithin(
                ST_Transform(p.way, 4326)::geography,
                -- Central station coordinates
                ST_SetSRID(ST_MakePoint(8.58309, 47.31763), 4326)::geography, 
                1000 
            )
        ORDER BY distance_meters;"""

# Query the database and store the result in a GeoDataFrame
gdf = gpd.GeoDataFrame.from_postgis(sql, engine)

# Dispose the engine
engine.dispose()

# Print the GeoDataFrame
gdf

#-------------------------------------------------------------------------------

#ST_SetSRID(ST_MakePoint(8.58309, 47.31763), 4326)::geography, #zuerst Lng, Lat
                #1000 Innerhalb Radius von 1000m


osm_id         shop    name  distance_meters                      geom
0  5791885827  supermarket    Coop       109.742700  POINT (8.58178 47.31806)
1  5791885768  supermarket  Migros       124.871828  POINT (8.58197 47.31846)

## Show selected features on map

In [157]:
# Ensure the GeoDataFrame has the correct projection (EPSG:4326)
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)
else:
    pass

# Calculate the mean longitude and latitude for the map center
centroids = gdf.geometry.centroid
lon = centroids.x.mean()
lat = centroids.y.mean()

# Initialize the map
m = folium.Map(location=[lat, lon], 
               zoom_start=16, #grössere Zahl = reingezoomt (braucht nur kleine Anpassungen)
               tiles='ESRIWorldImagery')

# Map settings
folium.GeoJson(
    gdf,
    name='map',
    popup=folium.GeoJsonPopup(fields=['name', 'distance_meters', 'shop']) # popups anpassen gemäss Spalten, welche zuvor ausgegeben werden
).add_to(m)

folium.LayerControl().add_to(m)

# Plot map
m

## Query: Select all roads classified as 'motorway' and create a 5000m buffer around these roads.

In [158]:
# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)

# Define SQL query (major roads)
sql = """-- Create buffer around major roads
        SELECT 
            1 as group_id,
            ST_TRANSFORM(ST_UNION(ST_Buffer(p.way::geometry, 5000)), 4326) AS geom
        FROM public.planet_osm_roads AS p
        WHERE
            highway = 'motorway';"""

# Query the database and store the result in a GeoDataFrame
gdf = gpd.GeoDataFrame.from_postgis(sql, engine, geom_col='geom')

# Dispose the engine
engine.dispose()

#-------------------------------------------------------------------------------

# ST_TRANSFORM(ST_UNION(ST_Buffer(p.way::geometry, 5000)), 4326) AS geom # 5000m buffer

## Show selected features on map

In [159]:
# Ensure the GeoDataFrame has the correct projection (EPSG:4326)
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)
else:
    pass

# Calculate the mean longitude and latitude for the map center
centroids = gdf.geometry.centroid
lon = centroids.x.mean()
lat = centroids.y.mean()

# Initialize the map
m = folium.Map(location=[lat, lon], 
               zoom_start=9, 
               tiles='EsriWorldTopoMap')

# Map settings
folium.GeoJson(
    gdf,
    name='map'
).add_to(m)

folium.LayerControl().add_to(m)

# Plot map
m

### Jupyter notebook --footer info-- (please always provide this at the end of each notebook)

In [160]:
import os
import platform
import socket
from platform import python_version
from datetime import datetime

print('-----------------------------------')
print(os.name.upper())
print(platform.system(), '|', platform.release())
print('Datetime:', datetime.now().strftime("%Y-%m-%d %H:%M:%S"))
print('Python Version:', python_version())
print('-----------------------------------')

-----------------------------------
POSIX
Linux | 6.5.0-1025-azure
Datetime: 2024-10-05 06:42:10
Python Version: 3.12.1
-----------------------------------
